# Import supporting package

In [1]:
import xarray as xr
import numpy as np

import matplotlib.pyplot as plt

from DataContainer.ReadData import read_hdf5_file
from Analyser.ImagingAnalyser import ImageAnalyser
from Analyser.FitAnalyser import FitAnalyser

imageAnalyser = ImageAnalyser()

## Start a client for parallel computing

In [2]:
from dask.distributed import Client
client = Client(n_workers=6, threads_per_worker=10, processes=True, memory_limit='10GB')
client

<Client: 'tcp://127.0.0.1:55356' processes=6 threads=60, memory=55.88 GiB>

# Read data

## Set file path

In [3]:
# filepath = "//DyLabNAS/Data/Evaporative_Cooling/2023/05/03/0043/*.h5"
# filepath = "//DyLabNAS/Data/Evaporative_Cooling/2023/04/18/0003/2023-04-18_0003_Evaporative_Cooling_000.h5"

filepath = "//DyLabNAS/Data/Repetition_scan/2023/04/21/0002/*.h5"

# filepath = r"./testData/0000/*.h5"

# filepath = "//DyLabNAS/Data/Evaporative_Cooling/2023/04/18/0003/*.h5"

In [4]:
groupList = [
    "images/MOT_3D_Camera/in_situ_absorption",
    # "images/ODT_1_Axis_Camera/in_situ_absorption",
]

dskey = {
    "images/MOT_3D_Camera/in_situ_absorption": "camera_1",
    # "images/ODT_1_Axis_Camera/in_situ_absorption": "camera_2",
}

dataSetDict = {
    dskey[groupList[i]]: read_hdf5_file(filepath, groupList[i])
    for i in range(len(groupList))
}

In [37]:
from datetime import date

today = date.today()
print("Today's date:", today)

d3 = today.strftime("%y/%m/%d")
print("d3 =", d3)
print(isinstance(d3, str))

Today's date: 2023-05-04
d3 = 23/05/04
True


## Rechunk the data for parallel computing

In [5]:
dataSet = dataSetDict["camera_1"]

scanAxis = dataSet.scanAxis

# dataSet = dataSet.chunk(
#     {
#         # "compZ_current_sg": "auto",
#         "sin_mod_freq": "auto",
#         "runs": 2,
#         "x": "auto",
#         "y": "auto",
#     }
# )

In [27]:
for key in dataset.dims.keys():
    print(key)

final_amp
runs
x
y


# Calculate absorption imaging

## get OD images

In [13]:
dataSet = imageAnalyser.get_absorption_images(dataSet)

dataSet

<xarray.Dataset>
Dimensions:     (final_amp: 11, runs: 3, x: 1200, y: 1920)
Coordinates:
  * final_amp   (final_amp) float64 3e-05 5.5e-05 8e-05 ... 0.000255 0.00028
  * runs        (runs) float64 0.0 1.0 2.0
Dimensions without coordinates: x, y
Data variables:
    atoms       (final_amp, runs, x, y) uint16 dask.array<chunksize=(1, 1, 1200, 1920), meta=np.ndarray>
    background  (final_amp, runs, x, y) uint16 dask.array<chunksize=(1, 1, 1200, 1920), meta=np.ndarray>
    dark        (final_amp, runs, x, y) uint16 dask.array<chunksize=(1, 1, 1200, 1920), meta=np.ndarray>
    shotNum     (final_amp, runs) <U2 '00' '11' '22' '01' ... '10' '21' '32'
    OD          (final_amp, runs, x, y) float64 dask.array<chunksize=(1, 1, 1200, 1920), meta=np.ndarray>
Attributes: (12/96)
    TOF_free:                          0.01
    abs_img_freq:                      110.858
    absorption_imaging_flag:           True
    backup_data:                       True
    blink_off_time:                    nan
    blink_on_time:                     nan
    ...                                ...
    z_offset:                          0.189
    z_offset_img:                      0.189
    final_amp:                         [3.00e-05 5.50e-05 8.00e-05 1.05e-04 1...
    runs:                              [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1...
    scanAxis:                          ['final_amp', 'runs']
    scanAxisLength:                    [33. 33.]

In [18]:
from ToolFunction.ToolFunction import *

remove_bad_shots(dataSet['OD'], runs=0)

<xarray.Dataset>
Dimensions:     (final_amp: 11, runs: 3, x: 1200, y: 1920)
Coordinates:
  * final_amp   (final_amp) float64 3e-05 5.5e-05 8e-05 ... 0.000255 0.00028
  * runs        (runs) float64 0.0 1.0 2.0
Dimensions without coordinates: x, y
Data variables:
    atoms       (final_amp, runs, x, y) uint16 98 101 109 106 ... 146 140 140
    background  (final_amp, runs, x, y) uint16 99 101 113 103 ... 147 137 137
    dark        (final_amp, runs, x, y) uint16 50 51 51 50 50 ... 50 51 50 49 49
    shotNum     (final_amp, runs) <U2 '00' '11' '22' '01' ... '10' '21' '32'
    OD          (final_amp, runs, x, y) float64 nan nan ... -0.03352 -0.03352
Attributes: (12/96)
    TOF_free:                          0.01
    abs_img_freq:                      110.858
    absorption_imaging_flag:           True
    backup_data:                       True
    blink_off_time:                    nan
    blink_on_time:                     nan
    ...                                ...
    z_offset:                          0.189
    z_offset_img:                      0.189
    final_amp:                         [3.00e-05 5.50e-05 8.00e-05 1.05e-04 1...
    runs:                              [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1...
    scanAxis:                          ['final_amp', 'runs']
    scanAxisLength:                    [33. 33.]

## Select region of interests

In [ ]:
imageAnalyser.center = (529, 962)
imageAnalyser.span = (100,100)
imageAnalyser.fraction = (0.1, 0.1)

# imageAnalyser.center = (890, 1150)
# imageAnalyser.span = (600,600)
# imageAnalyser.fraction = (0.1, 0.1)

# imageAnalyser.center = (890, 950)
# imageAnalyser.span = (100,100)
# imageAnalyser.fraction = (0.1, 0.1)

dataSet_crop = imageAnalyser.crop_image(dataSet)

In [ ]:
dataSet_crop.OD.isel(runs=[0]).plot.pcolormesh(cmap='jet', vmin=0, col=scanAxis[0], row=scanAxis[1])
# dataSet_crop.OD.plot()

## Remove the background

In [ ]:
dataSet_crop['OD'] = dataSet_crop['OD'] + 500

In [ ]:
dataSet_crop['OD'] = imageAnalyser.substract_offset(dataSet_crop['OD'])

# Test Fit

In [ ]:
fitAnalyser = FitAnalyser("Two Gaussian-2D", fitDim=2)

params = fitAnalyser.guess(dataSet_crop.OD, dask="parallelized")

In [ ]:
fitResult = fitAnalyser.fit(dataSet_crop.OD, params, dask="parallelized")

In [ ]:
fitCurve = fitAnalyser.eval(fitResult, x=np.arange(100), y=np.arange(100)).load()

In [ ]:
fitCurve.isel(**{scanAxis[0]:np.arange(30), 'runs':range(dataSet_crop.OD['runs'].size)}).plot.pcolormesh(cmap='jet', vmin=0, col=scanAxis[0], row=scanAxis[1])

# Get the Ncount

In [ ]:
Ncount = dataSet_crop.OD.sum(dim=(scanAxis[1], 'x', 'y'))

In [ ]:
fig = plt.figure()
Ncount.plot(fig=fig)